In [161]:
%reset

Once deleted, variables cannot be recovered. Proceed (y/[n])? y


In [3]:
import pandas as pd
import itertools
from pathlib import Path
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.validators.scatter.marker import SymbolValidator
import os
import seaborn as sns

## Load data

In [4]:
def cleanup_scenario_names(df_in):
    
    # todo: clean this up a little so it searches for scenarios that don't have an underscore
    
    # rename Today Actual --> Today Action_0_nan
    today_mask = np.array(df_in['Scenario'] == 'Today Actual')
    today_ids = list(np.where(today_mask)[0])
    df_in.iloc[today_ids, df_in.columns.get_loc('Scenario')] = 'Today Actual_0_nan'
    
    # rename Baseline --> Baseline_0_nan
    baseline_mask = np.array(df_in['Scenario'] == 'Baseline')
    baseline_ids = list(np.where(baseline_mask)[0])
    df_in.iloc[baseline_ids, df_in.columns.get_loc('Scenario')] = 'Baseline_0_nan'

    # turn all scenario names into a long name, short name, and line type
    df_in[['short_sce_name', 'line_id', 'long_sce_name']] = df_in['Scenario'].str.split("_", expand=True)
    df_in['line_id'] = df_in['line_id'].astype('int32')

    # long names that were NOT n/a will become short name + long name
    long_name_mask = np.array(df_in['long_sce_name'] != 'nan')
    long_name_ids = list(np.where(long_name_mask)[0])
    df_in.iloc[long_name_ids, df_in.columns.get_loc('long_sce_name')] = df_in.iloc[long_name_ids, df_in.columns.get_loc('short_sce_name')].astype(str) + " (" + df_in.iloc[long_name_ids, df_in.columns.get_loc('long_sce_name')] +")"

    # long names that were n/a will become short name
    short_name_ids = list(np.where(np.invert(long_name_mask))[0])
    display(df_in)
    df_in.iloc[short_name_ids, df_in.columns.get_loc('long_sce_name')] = df_in.iloc[short_name_ids, df_in.columns.get_loc('short_sce_name')]
    
    return df_in

In [5]:
input_path = Path("resultsFiles/mar6_2023")

# folder to store combined csv of all results
csv_path = input_path / Path('combinedCSV')
csv_path.mkdir(parents=True, exist_ok=True)

# load csv
df = pd.read_csv(csv_path / 'combined_results.csv', header=0, index_col=0)
df = cleanup_scenario_names(df)
df.head()

Demand\Agriculture  Demand\Commercial  Demand\Industry  \
2018        2.637486e+06       1.370354e+07     2.860969e+07   
2019        2.637486e+06       1.370354e+07     2.860969e+07   
2020        2.637486e+06       1.370354e+07     2.860969e+07   
2021        2.637486e+06       1.370354e+07     2.860969e+07   
2022        2.637486e+06       1.370354e+07     2.860969e+07   
...                  ...                ...              ...   
2041        0.000000e+00       0.000000e+00     0.000000e+00   
2042        0.000000e+00       0.000000e+00     0.000000e+00   
2043        0.000000e+00       0.000000e+00     0.000000e+00   
2044        0.000000e+00       0.000000e+00     0.000000e+00   
2045        0.000000e+00       0.000000e+00     0.000000e+00   

      Demand\Remaining Electricity  Demand\Residential  \
2018                           0.0        2.863188e+07   
2019                           0.0        2.852815e+07   
2020                           0.0        2.847535e+07   
2021                           0.0        2.847496e+07   
2022                           0.0        2.848175e+07   
...                            ...                 ...   
2041                           0.0        0.000000e+00   
2042                           0.0        0.000000e+00   
2043                           0.0        0.000000e+00   
2044                           0.0        0.000000e+00   
2045                           0.0        0.000000e+00   

      Demand\Transportation\Aviation  Demand\Transportation\HDVs  \
2018                    4.926126e+06                4.468765e+07   
2019                    4.926126e+06                4.498742e+07   
2020                    4.926126e+06                4.527512e+07   
2021                    4.926126e+06                4.554300e+07   
2022                    4.926126e+06                4.577655e+07   
...                              ...                         ...   
2041                    0.000000e+00                0.000000e+00   
2042                    0.000000e+00                0.000000e+00   
2043                    0.000000e+00                0.000000e+00   
2044                    0.000000e+00                0.000000e+00   
2045                    0.000000e+00                0.000000e+00   

      Demand\Transportation\LDVs  Demand\Transportation\Rail  \
2018                1.184452e+08                2.296612e+06   
2019                1.149979e+08                2.296612e+06   
2020                1.118519e+08                2.296612e+06   
2021                1.089850e+08                2.296612e+06   
2022                1.063776e+08                2.296612e+06   
...                          ...                         ...   
2041                0.000000e+00                0.000000e+00   
2042                0.000000e+00                0.000000e+00   
2043                0.000000e+00                0.000000e+00   
2044                0.000000e+00                0.000000e+00   
2045                0.000000e+00                0.000000e+00   

      Demand\Transportation\Water Borne  ...  \
2018                       3.878970e+06  ...   
2019                       3.878970e+06  ...   
2020                       3.878970e+06  ...   
2021                       3.878970e+06  ...   
2022                       3.878970e+06  ...   
...                                 ...  ...   
2041                       0.000000e+00  ...   
2042                       0.000000e+00  ...   
2043                       0.000000e+00  ...   
2044                       0.000000e+00  ...   
2045                       0.000000e+00  ...   

     Transformation\Hydrogen TDS\Output Fuels\Hydrogen Transmitted  \
2018                                                0.0              
2019                                                0.0              
2020                                                0.0              
2021                                                0.0              
2022                       

Demand\Agriculture  Demand\Commercial  Demand\Industry  \
2018        2.637486e+06       1.370354e+07     2.860969e+07   
2019        2.637486e+06       1.370354e+07     2.860969e+07   
2020        2.637486e+06       1.370354e+07     2.860969e+07   
2021        2.637486e+06       1.370354e+07     2.860969e+07   
2022        2.637486e+06       1.370354e+07     2.860969e+07   

      Demand\Remaining Electricity  Demand\Residential  \
2018                           0.0        2.863188e+07   
2019                           0.0        2.852815e+07   
2020                           0.0        2.847535e+07   
2021                           0.0        2.847496e+07   
2022                           0.0        2.848175e+07   

      Demand\Transportation\Aviation  Demand\Transportation\HDVs  \
2018                    4.926126e+06                4.468765e+07   
2019                    4.926126e+06                4.498742e+07   
2020                    4.926126e+06                4.527512e+07   
2021                    4.926126e+06                4.554300e+07   
2022                    4.926126e+06                4.577655e+07   

      Demand\Transportation\LDVs  Demand\Transportation\Rail  \
2018                1.184452e+08                2.296612e+06   
2019                1.149979e+08                2.296612e+06   
2020                1.118519e+08                2.296612e+06   
2021                1.089850e+08                2.296612e+06   
2022                1.063776e+08                2.296612e+06   

      Demand\Transportation\Water Borne  ...  \
2018                       3.878970e+06  ...   
2019                       3.878970e+06  ...   
2020                       3.878970e+06  ...   
2021                       3.878970e+06  ...   
2022                       3.878970e+06  ...   

     Transformation\Hydrogen TDS\Output Fuels\Hydrogen Transmitted  \
2018                                                0.0              
2019                                                0.0              
2020                                                0.0              
2021                                                0.0              
2022                                                0.0              

      Transformation\Hydrogen TDS\Processes\Hydrogen TDS  \
2018                                                0.0    
2019                                                0.0    
2020                                                0.0    
2021                                                0.0    
2022                                                0.0    

      Transformation\NG Compressors  Transformation\RNG Production  \
2018                   1.499823e+06                            0.0   
2019                   1.497122e+06                            0.0   
2020                   1.496271e+06                            0.0   
2021                   1.497041e+06                            0.0   
2022                   1.498120e+06                            0.0   

      Transformation\Refinery FCCU and CHP  \
2018                          2.115238e+07   
2019                          2.063032e+07   
2020                          2.015491e+07   
2021                          1.972297e+07   
2022                          1.933016e+07   

      Transformation\Renewable Diesel Refining  \
2018                                  0.000417   
2019                                  0.000417   
2020                                  0.000417   
2021                                  0.000417   
2022                                  0.000417   

      Transformation\Steam Generators  short_sce_name  line_id  long_sce_name  
2018                     1.234632e+07        Baseline        0       Baseline  
2019                     1.234632e+07        Baseline        0       Baseline  
2020                     1.234632e+07        Baseline        0       Baseline  
2021                     1.234632e+07        Baseline        0       Baseline  
2022    

In [6]:
# TODO: obviously change this !!!

IMAGE_COUNT = 0
IMAGE_PATH = input_path / 'figures'
IMAGE_PATH.mkdir(parents=True, exist_ok=True)

### Identifier columns remaining in the df

In [413]:
id_cols = ['Scenario', 'Result Variable', 'Fuel', 'line_id', 'short_sce_name', 'long_sce_name']
for col in id_cols:
    print()
    print(f"{col}: ")
    print(df[col].unique())


Scenario: 
['Baseline_0_nan' 'LEAP Version CARB Reference_0_nan'
 'LEAP Version CARB Proposed_0_nan' 'Mixed Scenario 2045_0_nan'
 'Mixed Scenario 2045_1_incentives extended'
 'Mixed Scenario 2045_2_in state incentives off'
 'Mixed Scenario 2045_3_aggressive learning rate'
 'Mixed Scenario 2045_4_modest learning rate' 'Mixed Scenario 2035_0_nan'
 'Mixed Scenario 2035_1_incentives extended'
 'Mixed Scenario 2035_2_in state incentives off'
 'Mixed Scenario 2035_3_aggressive learning rate'
 'Mixed Scenario 2035_4_modest learning rate']

Result Variable: 
['One_Hundred Year GWP Direct At Point of Emissions' 'Social Costs'
 'Energy Demand Final Units' 'Inputs' 'Outputs by Output Fuel'
 'Imports Into Module' 'Exports From Module' 'Capacity' 'Capacity Added'
 'Imports' 'Exports']

Fuel: 
['Total' 'Other' 'Gasoline' 'Diesel' 'Electricity' 'Hydrogen Transmitted'
 'CRNG' 'Ethanol' 'Renewable Diesel']

line_id: 
[0 1 2 3 4]

short_sce_name: 
['Baseline' 'LEAP Version CARB Reference' 'LEAP Version

## Setup line styles and assign a color to each scenario group

In [414]:
scenarios = df["Scenario"].unique().tolist()

# scenario comparisons where we want the short scenario name in the legend
sce_comps_short = [
    scenarios,
    [s for s in scenarios if ("2035" in s) or ("2045" in s)],
]

# scenario comparisons where we want the long scenario name in the legend
sce_comps_long = [
    [s for s in scenarios if "2035" in s],
    [s for s in scenarios if "2045" in s],
    [s for s in scenarios if "_0_" in s],
    [s for s in scenarios if "incentives extended" in s],
    [s for s in scenarios if "learning rate" in s],
]

# https://datascience.stackexchange.com/questions/106908/plotly-scatter-plot-what-are-the-possible-options-for-the-dash-entry-in-the-li
# TODO: update dash-dict so it is easier to distinguish different lines
dash_dict = {
    0 : 'solid',
    1: '2, 2, 2, 2',
    2: '8, 2, 8, 2',
    3: '12, 2, 3, 2',
    4: '8, 8, 8, 8',
}

# unique color is assigned to each scenario group (ie where short sce name is the same)
color_dict = dict(zip(df['short_sce_name'].unique(), px.colors.qualitative.D3))
if len(color_dict) != len(df['short_sce_name'].unique()):
    print("Warning: some scenarios do not have assigned colors")

## Emissions or marginal cost over time by scenario (line)

In [415]:
def form_df_emis_cost_time_sce(
    df_in, 
    result_str, 
    marginalize=False, 
    relative_to="LEAP Version CARB Reference_0_nan",
):

    id_cols = ['Scenario', 'Result Variable', 'Fuel', 'line_id', 'short_sce_name', 'long_sce_name']
    result_cols = list(set(df_in.columns) - set(id_cols))

    # iterate through scenarios
    df_out = pd.DataFrame()
    for sce, dfg in df[df['Result Variable'] == result_str].groupby('Scenario'):
        dfg_result = pd.DataFrame(index=df.index.unique(), 
                                  columns=['Result', 'Scenario', 'line_id', 'short_sce_name', 'long_sce_name'])
        dfg_result['Result'] = dfg[result_cols].sum(axis=1)
        dfg_result[['Scenario', 'line_id', 'short_sce_name', 'long_sce_name']] = dfg[['Scenario', 'line_id', 'short_sce_name', 'long_sce_name']]
        df_out = pd.concat([df_out, dfg_result])
    
    # make year its own column instead of using it as the index
    df_out.reset_index(inplace=True)
    df_out.rename({'index' : 'year'}, axis=1, inplace=True)
        
    # marginalie result relative to 'relative_to' scenario
    if marginalize:
        for yr in df_out['year'].unique():
            yr_mask = np.array(df_out['year'] == yr)
            yr_mask_ids = list(np.where(yr_mask)[0])
            relative_to_sce_mask = np.array((df_out['Scenario'] == relative_to) &
                                            (df_out['year'] == yr))
            relative_to_sce_id = list(np.where(relative_to_sce_mask)[0])
            df_out.iloc[yr_mask_ids, df_out.columns.get_loc('Result')] -= float(df_out.iloc[relative_to_sce_id, df_out.columns.get_loc('Result')])
    
    return df_out

In [416]:
def plot_emis_or_cost_time(df_in, sce, title, yaxis_title, xaxis_title, 
                           color_dict, dash_dict, legend_names='long'):
    fig = go.Figure()
    
    # iterate through scenarios
    for _, dfg in df_in[df_in['Scenario'].isin(sce)].groupby('Scenario'):        
        
        # figure out what goes into the legend
        if legend_names == 'long':
            name = dfg['long_sce_name'].unique()[0]
            showlegend = True
        else:
            name = dfg['short_sce_name'].unique()[0]
            showlegend = bool(dfg['line_id'].unique()[0] == 0)
        
        # set color and line style
        col = color_dict[dfg['short_sce_name'].unique()[0]]
        line_sty = dash_dict[dfg['line_id'].unique()[0]]
        
        # add line to graph
        fig.add_trace(go.Scatter(
            mode='lines',
            x=dfg['year'],
            y=dfg['Result'],
            name=name,
            showlegend=showlegend,
            line=dict(
                color=col,
                dash=line_sty,
            )
        ))
        
    # update title and axis titles
    fig.update_layout(
        title=title,
        xaxis_title=xaxis_title,
        yaxis_title=yaxis_title,
    )
    fig.update_yaxes(rangemode="tozero")
    
    global IMAGE_PATH
    global IMAGE_COUNT
    fig.write_image(IMAGE_PATH / f"fig_{IMAGE_COUNT}.pdf")
    IMAGE_COUNT += 1
    fig.show()    

In [417]:
emissions_result_str = 'One_Hundred Year GWP Direct At Point of Emissions'
cost_result_str = 'Social Costs'

df_emissions = form_df_emis_cost_time_sce(df, emissions_result_str)
df_marg_cost = form_df_emis_cost_time_sce(df, cost_result_str, marginalize=True)

for comp_group, legend_name_len in zip([sce_comps_short, sce_comps_long], ['short', 'long']):
    for sce_comp in comp_group:
        plot_emis_or_cost_time(
            df_emissions, 
            sce=sce_comp, 
            title='Scenario Emissions', 
            yaxis_title='Annual Emissions (Tonnes CO2e)', 
            xaxis_title='Year',                        
            color_dict=color_dict, 
            dash_dict=dash_dict, 
            legend_names=legend_name_len,
        )
        plot_emis_or_cost_time(
            df_marg_cost, 
            sce=sce_comp, 
            title='Scenario Marginal Costs', 
            yaxis_title='USD/yr', 
            xaxis_title='Year',                        
            color_dict=color_dict, 
            dash_dict=dash_dict, 
            legend_names=legend_name_len,
        )

## Marginally abated emissions vs marginally abated costs across scenarios (scatter)
## And cost of carbon abatement USD/Tonne compared across scenarios (bar)

In [418]:
def form_df_marg_emis_marg_cost(df_in, relative_to="LEAP Version CARB Reference_0_nan", disc_rate=0.05):
    
    id_cols = ['Scenario', 'Result Variable', 'Fuel', 'line_id', 'short_sce_name', 'long_sce_name']
    result_cols = list(set(df.columns) - set(id_cols))
    emis_res_str = 'One_Hundred Year GWP Direct At Point of Emissions'
    cost_res_str = 'Social Costs'
    
    df_out = pd.DataFrame(columns=['Emissions', 'Cost', 'Scenario', 'line_id', 'short_sce_name', 'long_sce_name'])
    
    for sce, dfg in df_in.groupby('Scenario'):
        cum_emis = dfg[result_cols][dfg['Result Variable'] == emis_res_str].sum(axis=0).sum()
        annual_cost = dfg[result_cols][dfg['Result Variable'] == cost_res_str].sum(axis=1)
        npv = 0
        base_yr = annual_cost.index.min()
        for yr in annual_cost.index:
            npv += annual_cost[yr] / (1 + disc_rate)**(yr - base_yr)
        df_out.loc[len(df_out.index)] = [cum_emis, npv, sce, 
                                         dfg['line_id'].unique()[0], 
                                         dfg['short_sce_name'].unique()[0], 
                                         dfg['long_sce_name'].unique()[0]]
        
    df_out = df_out.set_index('Scenario')
    df_out['marg_abated_emis'] = float(df_out.loc[relative_to, 'Emissions']) - df_out['Emissions']
    df_out['marg_cost'] = df_out['Cost'] - float(df_out.loc[relative_to, 'Cost'])
    df_out['cost_per_emis'] = df_out['marg_cost'] / df_out['marg_abated_emis']
    
    # rename weird scenario name that we use in excel into short name, long name, and line type
    df_out.reset_index(inplace=True)
    df_out.rename({'index' : 'Scenario'}, axis=1, inplace=True)
    
    return df_out

    
def plot_emis_cost_scatter(df_in, sce, title, ycol, yaxis_title, xcol, xaxis_title, 
                           color_dict, legend_names='long'):
    
    markers = [0, 3, 4, 5, 13, 18, 19]
    fig = go.Figure()
    
    # iterate through scenarios
    for _, dfg in df_in[df_in['Scenario'].isin(sce)].groupby('Scenario'):
              
        dfg_series = dfg.squeeze()
        
        # figure out what goes into the legend
        if legend_names == 'long':
            name = dfg_series['long_sce_name']
            showlegend = True
        else:
            name = dfg_series['short_sce_name']
            showlegend = bool(dfg_series['line_id'] == 0)
        
        # set color and line style
        col = color_dict[dfg_series['short_sce_name']]
        
        # add scatter to graph
        fig.add_trace(go.Scatter(
            mode='markers',
            x=[dfg_series[xcol]],
            y=[dfg_series[ycol]],
            name=name,
            showlegend=showlegend,
            marker_symbol=200 + markers[dfg_series['line_id']],
            marker_color=col
        ))
        
    # update title and axis titles
    fig.update_layout(
        title=title,
        xaxis_title=xaxis_title,
        yaxis_title=yaxis_title,
    )
    fig.update_traces(marker={'size' : 12})
    
    global IMAGE_PATH
    global IMAGE_COUNT
    fig.write_image(IMAGE_PATH / f"fig_{IMAGE_COUNT}.pdf")
    IMAGE_COUNT += 1
    
    fig.show()
    
def plot_cost_mitigation_bar(df_in, sce, color_dict):
    fig = px.bar(
        data_frame=df_in[df_in['Scenario'].isin(sce)],
        x='cost_per_emis',
        y='long_sce_name',
        color='short_sce_name',
        color_discrete_map=color_dict,
        title='Cost of Carbon Mitigation'
    )
    fig.update_layout(
        xaxis_title="USD / tonne CO2e",
        yaxis_title="Scenario",
        showlegend=False,
    )
    
    global IMAGE_PATH
    global IMAGE_COUNT
    fig.write_image(IMAGE_PATH / f"fig_{IMAGE_COUNT}.pdf")
    IMAGE_COUNT += 1
    
    fig.show()

In [419]:
df_marg_emis_marg_cost = form_df_marg_emis_marg_cost(df)

plot_cost_mitigation_bar(df_marg_emis_marg_cost, scenarios, color_dict)

for comp_group, legend_name_len in zip([sce_comps_short, sce_comps_long], ['short', 'long']):
    for sce_comp in comp_group:
        plot_emis_cost_scatter(
            df_in=df_marg_emis_marg_cost, 
            sce=sce_comp, 
            title='Abatement Emissions vs Cost', 
            ycol='marg_cost', 
            yaxis_title='Marginal Cost (USD)', 
            xcol='marg_abated_emis', 
            xaxis_title='Marginal Abated Emissions (tonnes CO2e)',               
            color_dict=color_dict, 
            legend_names=legend_name_len,
        )


## Comparison against carb - emissions over time (line)

In [420]:
# folder to store combined csv of all results
carb_path = input_path / Path('carb_results')
carb_path.mkdir(parents=True, exist_ok=True)

# load csv
df_carb = pd.read_excel(carb_path / 'carb_summary.xlsx', header=0, index_col=None)
df_carb['line_id'] = 1
df_carb['long_sce_name'] = df_carb['Scenario']
df_carb['short_sce_name'] = df_carb['Scenario']

leap_carb_sce = [s for s in scenarios if "CARB" in s]
df_emissions = form_df_emis_cost_time_sce(df, emissions_result_str)

df_emissions = df_emissions[df_emissions['Scenario'].isin(leap_carb_sce)]

df_emissions = pd.concat([df_emissions, df_carb], sort=True)

color_dict['CARB Reference'] = color_dict['LEAP Version CARB Reference']
color_dict['CARB Proposed'] = color_dict['LEAP Version CARB Proposed']


plot_emis_or_cost_time(
    df_emissions, 
    sce=df_emissions['Scenario'].unique(), 
    title='Scenario Emissions - CARB Comparison', 
    yaxis_title='Annual Emissions (Tonnes CO2e)', 
    xaxis_title='Year',                        
    color_dict=color_dict, 
    dash_dict=dash_dict, 
    legend_names='long',
)

## Egen output by resource in specified year (bar)

## Egen output over time by resource (area)

In [421]:
# form dictionary mapping branches to their egen resource
egen_res_map = {
    'Biogas' : [],
    'Biomass' : [],
    'Coal' : [],
    'Geothermal' : [],
    'H2 Fuel Cell' : [],
    'Hydro' : [],
    'Li Ion' : [],
    'Natural Gas' : [],
    'Natural Gas CCS' : [],
    'Nuclear' : [],
    'Solar' : [],
    'Unspecified' : [],
    'Wind' : [],   
}


egen_branches = [col for col in df.columns if "Transformation\Electricity Production" in col]

for branch in egen_branches:
    if ('landfill' in branch.lower()) or ('manure' in branch.lower()) or ('wwtp' in branch.lower()) or ('food' in branch.lower()):
        egen_res_map['Biogas'].append(branch)
    elif ('biomass' in branch.lower()) or ('solid waste' in branch.lower()):
        egen_res_map['Biomass'].append(branch)
    elif 'coal' in branch.lower():
        egen_res_map['Coal'].append(branch)
    elif 'geothermal' in branch.lower():
        egen_res_map['Geothermal'].append(branch)
    elif 'hydrogen fuel cell' in branch.lower():
        egen_res_map['H2 Fuel Cell'].append(branch)
    elif 'hydro' in branch.lower():
        egen_res_map['Hydro'].append(branch)
    elif 'li ion' in branch.lower():
        egen_res_map['Li Ion'].append(branch)
    elif 'gas css' in branch.lower():
        egen_res_map['Natural Gas CCS'].append(branch)
    elif ('natural gas' in branch.lower()) or ('ng' in branch.lower()):
        egen_res_map['Natural Gas'].append(branch)
    elif 'nuclear' in branch.lower():
        egen_res_map['Nuclear'].append(branch)
    elif 'solar' in branch.lower():
        egen_res_map['Solar'].append(branch)
    elif 'unspecified' in branch.lower():
        egen_res_map['Unspecified'].append(branch)
    elif 'wind' in branch.lower():
        egen_res_map['Wind'].append(branch)
    else:
        print(f"Branch: {branch} not assigned")

egen_res_map_short = {
    'Other' : egen_res_map['Coal'] + egen_res_map['Geothermal'] + egen_res_map['Nuclear'] + egen_res_map['Unspecified'] + egen_res_map['Biogas'] + egen_res_map['Biomass'],
    'H2 Fuel Cell' : egen_res_map['H2 Fuel Cell'],
    'Li Ion' : egen_res_map['Li Ion'],
    'Hydro' : egen_res_map['Hydro'],
    'Natural Gas' : egen_res_map['Natural Gas'],
    'Natural Gas CCS' : egen_res_map['Natural Gas CCS'],
    'Solar' : egen_res_map['Solar'],
    'Wind' : egen_res_map['Wind'],   
}

def rgb_to_hex(r, g, b):
    return '#{:02x}{:02x}{:02x}'.format(r, g, b)

egen_res_color_map = dict(zip(list(egen_res_map.keys()) + ['Other'], px.colors.qualitative.Light24))
if len(egen_res_map.keys()) + 1 != len(egen_res_color_map.keys()):
    print("Warning: some egen resources do not have an assigned color")

Branch: Transformation\Electricity Production Exogenous\Output Fuels\Electricity Untransmitted not assigned
Branch: Transformation\Electricity Production Optimal\Output Fuels\Electricity Untransmitted not assigned


In [422]:
def form_df_result_by_subgroup(df_in, branch_map, result_str):
    
    id_cols = ['Scenario', 'line_id', 'short_sce_name', 'long_sce_name']
    result_cols = branch_map.keys()
    df_out = pd.DataFrame()
    for sce, dfg in df_in[df_in['Result Variable'] == result_str].groupby('Scenario'):
        for subgroup in branch_map.keys():
            dfg_result = pd.DataFrame()
            dfg_result['Value'] = dfg[branch_map[subgroup]].sum(axis=1)
            dfg_result['Subgroup'] = subgroup
            dfg_result[id_cols] = dfg[id_cols]
            dfg_result['Year'] = dfg.index
            df_out = pd.concat([df_out, dfg_result], sort=True)
    return df_out.reset_index(drop=True)

def plot_subgroup_result_over_time(df_in, title, units, color_map, graph_type='bar'):
    for sce, dfg in df_in.groupby('Scenario'):
          
        if graph_type == 'bar':
            fig = px.bar(
                dfg, 
                x='Year', 
                y='Value', 
                color='Subgroup',
                color_discrete_map=color_map,
            )
            dfg_sum = pd.DataFrame(columns = ['Year', 'Value'])
            for yr in dfg['Year'].unique():
                annual_sum = dfg['Value'][dfg['Year'] == yr].sum()
                dfg_sum.loc[len(dfg_sum.index)] = [yr, annual_sum]
            # add line to graph showing cumulative sum
            fig.add_trace(go.Scatter(
                mode='lines',
                x=dfg_sum['Year'],
                y=dfg_sum['Value'],
                name="Annual Sum",
                showlegend=True,
                line=dict(
                    color='black',
                    dash='solid',
                )
            ))
        else:
            fig = px.area(
                dfg, 
                x='Year', 
                y='Value', 
                color='Subgroup',
                color_discrete_map=color_map,
            )
            # remove line from top of area graph
            for i in range(len(fig['data'])):
                fig['data'][i]['line']['width']=0
        
        fig.update_layout(
            title=title + f": {dfg['long_sce_name'].unique()[0]}",
            xaxis_title='Year',
            yaxis_title=units,
        )
        
        global IMAGE_PATH
        global IMAGE_COUNT
        fig.write_image(IMAGE_PATH / f"fig_{IMAGE_COUNT}.pdf")
        IMAGE_COUNT += 1
        
        fig.show()

def plot_subgroup_result_single_yr_compare_scenarios(df_in, sce, title, units, yr, color_map):
    mask = np.array(
        (df_in['Year'] == yr) & 
        (df_in['Scenario'].isin(sce))
    )
    ids = list(np.where(mask)[0])
        
    fig = px.bar(
        df_in.iloc[ids, :],
        x='Value',
        y='long_sce_name',
        color='Subgroup',
        color_discrete_map=color_map,
    )
    fig.update_layout(
        xaxis_title=units,
        yaxis_title='',
        title=title + f" in {yr}",
    )
    
    global IMAGE_PATH
    global IMAGE_COUNT
    fig.write_image(IMAGE_PATH / f"fig_{IMAGE_COUNT}.pdf")
    IMAGE_COUNT += 1
    
    fig.show()

In [423]:
df_egen_production_by_resource = form_df_result_by_subgroup(df, egen_res_map, "Outputs by Output Fuel")
df_egen_production_by_resource_short = form_df_result_by_subgroup(df, egen_res_map_short, "Outputs by Output Fuel")
df_egen_production_by_resource

Scenario Subgroup         Value  Year  \
0                                 Baseline_0_nan   Biogas  2.127211e+07  2018   
1                                 Baseline_0_nan   Biogas  2.108284e+07  2019   
2                                 Baseline_0_nan   Biogas  2.089357e+07  2020   
3                                 Baseline_0_nan   Biogas  2.070431e+07  2021   
4                                 Baseline_0_nan   Biogas  2.051504e+07  2022   
...                                          ...      ...           ...   ...   
4727  Mixed Scenario 2045_4_modest learning rate     Wind  1.947348e+08  2041   
4728  Mixed Scenario 2045_4_modest learning rate     Wind  1.947348e+08  2042   
4729  Mixed Scenario 2045_4_modest learning rate     Wind  1.947348e+08  2043   
4730  Mixed Scenario 2045_4_modest learning rate     Wind  1.947348e+08  2044   
4731  Mixed Scenario 2045_4_modest learning rate     Wind  2.158407e+08  2045   

      line_id                               long_sce_name       short_sce_name  
0           0                                    Baseline             Baseline  
1           0                                    Baseline             Baseline  
2           0                                    Baseline             Baseline  
3           0                                    Baseline             Baseline  
4           0                                    Baseline             Baseline  
...       ...                                         ...                  ...  
4727        4  Mixed Scenario 2045 (modest learning rate)  Mixed Scenario 2045  
4728        4  Mixed Scenario 2045 (modest learning rate)  Mixed Scenario 2045  
4729        4  Mixed Scenario 2045 (modest learning rate)  Mixed Scenario 2045  
4730        4  Mixed Scenario 2045 (modest learning rate)  Mixed Scenario 2045  
4731        4  Mixed Scenario 2045 (modest learning rate)  Mixed Scenario 2045  

[4732 rows x 7 columns]

In [424]:
for sce in sce_comps_short + sce_comps_long:
    plot_subgroup_result_single_yr_compare_scenarios(
        df_egen_production_by_resource, 
        sce, "Egen by Resource", "GJ", 2045, egen_res_color_map)
    plot_subgroup_result_single_yr_compare_scenarios(
        df_egen_production_by_resource_short, 
        sce, "Egen by Resource", "GJ", 2045, egen_res_color_map)


In [425]:
plot_subgroup_result_over_time(
    df_egen_production_by_resource, 
    "Egen by Resource", "GJ", egen_res_color_map, "area")
plot_subgroup_result_over_time(
    df_egen_production_by_resource_short, 
    "Egen by Resource", "GJ", egen_res_color_map, "area")

## Egen capacity added (bar)

In [426]:
df_egen_capacity_added_by_resource = form_df_result_by_subgroup(df, egen_res_map, "Capacity Added")
df_egen_capacity_added_by_resource_short = form_df_result_by_subgroup(df, egen_res_map_short, "Capacity Added")
df_egen_capacity_added_by_resource

Scenario Subgroup    Value  Year  \
0                                 Baseline_0_nan   Biogas     0.00  2018   
1                                 Baseline_0_nan   Biogas     0.00  2019   
2                                 Baseline_0_nan   Biogas     0.00  2020   
3                                 Baseline_0_nan   Biogas     0.00  2021   
4                                 Baseline_0_nan   Biogas     0.00  2022   
...                                          ...      ...      ...   ...   
4727  Mixed Scenario 2045_4_modest learning rate     Wind     0.00  2041   
4728  Mixed Scenario 2045_4_modest learning rate     Wind     0.00  2042   
4729  Mixed Scenario 2045_4_modest learning rate     Wind     0.00  2043   
4730  Mixed Scenario 2045_4_modest learning rate     Wind     0.00  2044   
4731  Mixed Scenario 2045_4_modest learning rate     Wind  2711.74  2045   

      line_id                               long_sce_name       short_sce_name  
0           0                                    Baseline             Baseline  
1           0                                    Baseline             Baseline  
2           0                                    Baseline             Baseline  
3           0                                    Baseline             Baseline  
4           0                                    Baseline             Baseline  
...       ...                                         ...                  ...  
4727        4  Mixed Scenario 2045 (modest learning rate)  Mixed Scenario 2045  
4728        4  Mixed Scenario 2045 (modest learning rate)  Mixed Scenario 2045  
4729        4  Mixed Scenario 2045 (modest learning rate)  Mixed Scenario 2045  
4730        4  Mixed Scenario 2045 (modest learning rate)  Mixed Scenario 2045  
4731        4  Mixed Scenario 2045 (modest learning rate)  Mixed Scenario 2045  

[4732 rows x 7 columns]

In [427]:
def make_cumulative(df_in):
    yrs = np.sort(df_in['Year'].unique())
    for key, dfg in df_in.groupby(by=['Scenario', 'Subgroup']):
        mask = np.array(
            (df_in['Scenario'] == key[0]) & 
            (df_in['Subgroup'] == key[1])
        )
        ids = list(np.where(mask)[0])
        df_in.iloc[ids, df_in.columns.get_loc('Value')] = dfg['Value'].cumsum()
    
    return df_in

In [428]:
df_egen_capacity_added_by_resource = make_cumulative(df_egen_capacity_added_by_resource)
df_egen_capacity_added_by_resource_short = make_cumulative(df_egen_capacity_added_by_resource_short)


In [429]:
for sce in sce_comps_short + sce_comps_long:
    plot_subgroup_result_single_yr_compare_scenarios(
        df_egen_capacity_added_by_resource, 
        sce, "Cumulative Capacity Added by Resource", "MW", 2045, egen_res_color_map)
    plot_subgroup_result_single_yr_compare_scenarios(
        df_egen_capacity_added_by_resource_short, 
        sce, "Cumulative Capacity Added by Resource", "MW", 2045, egen_res_color_map)

In [430]:
plot_subgroup_result_over_time(
    df_egen_capacity_added_by_resource, 
    "Cumulative Capacity Added by Resource", "MW", egen_res_color_map)
plot_subgroup_result_over_time(
    df_egen_capacity_added_by_resource_short, 
    "Cumulative Capacity Added by Resource", "MW", egen_res_color_map)

## TODO: Emissions and cost over time by sector (area)

## Emissions by sector compared across scenarios in a specified year (bar)

In [431]:
# form dictionary mapping branches to their sector
sector_map = {
    'Industry' : [],
    'Electricity' : [],
    'Buildings' : [],
    'Agriculture' : [],
    'Transportation' : [],
    'Resources' : [],
    'Incentives' : [],
}

for branch in list(set(df.columns) - set(id_cols)):
    if (
        ('Demand\Residential' in branch) or 
        ('Demand\Commercial' in branch) or 
        ('Non Energy\Residential' in branch) or 
        ('Non Energy\Commercial' in branch)
    ):
        sector_map['Buildings'].append(branch)
    elif (
        ('Demand\Transportation' in branch) or
        ('Non Energy\Transportation' in branch)
    ):
        sector_map['Transportation'].append(branch)
    elif (
        ('Demand\Agriculture' in branch) or
        ('Non Energy\Agriculture' in branch)
    ):
        sector_map['Agriculture'].append(branch)
    elif (
        ('Demand\Industry' in branch) or
        ('Transformation\Ethanol' in branch) or
        ('Transformation\Biodiesel' in branch) or 
        ('Transformation\Refinery' in branch) or
        ('Transformation\Renewable Diesel' in branch) or
        ('Transformation\Crude Oil' in branch) or
        ('Transformation\Steam Gen' in branch) or
        ('Transformation\Hydrogen' in branch) or
        ('Transformation\CNG' in branch) or
        ('Transformation\CRNG' in branch) or
        ('Transformation\RNG' in branch) or
        ('NG Compressors' in branch) or
        ('Non Energy\Industry' in branch) or
        ('Non Energy\Carbon Removal\Industry' in branch) or
        ('Non Energy\Carbon Removal\DAC' in branch)
    ):
        sector_map['Industry'].append(branch)
    
    elif (
        ('Transformation\Electricity' in branch) or
        ('Non Energy\Electricity' in branch) or
        ('Transformation\Distributed PV' in branch) or 
        ('Carbon Removal\Electricity Production' in branch)
    ):
        sector_map['Electricity'].append(branch)
    elif (
        ('Resources\\' in branch)
    ):
        sector_map['Resources'].append(branch)
    elif (
        ('Non Energy\Incentives' in branch)
    ):
        sector_map['Incentives'].append(branch)
    else:
        print(f"branch: {branch} not added to mapping")

sector_color_map = {
    'Industry' : "#3366CC",
    'Electricity' : "#9467BD",
    'Buildings' : "#FECB52",
    'Agriculture' : "#109618",
    'Transportation' : "#B82E2E",
    'Resources' : "#FF97FF",
}

branch: Demand\Remaining Electricity not added to mapping


In [432]:
df_emissions_sector = form_df_result_by_subgroup(df, sector_map, 'One_Hundred Year GWP Direct At Point of Emissions')
df_emissions_sector

Scenario    Subgroup         Value  \
0                                 Baseline_0_nan    Industry  9.303381e+07   
1                                 Baseline_0_nan    Industry  9.232878e+07   
2                                 Baseline_0_nan    Industry  9.168558e+07   
3                                 Baseline_0_nan    Industry  9.109994e+07   
4                                 Baseline_0_nan    Industry  9.056498e+07   
...                                          ...         ...           ...   
2543  Mixed Scenario 2045_4_modest learning rate  Incentives  0.000000e+00   
2544  Mixed Scenario 2045_4_modest learning rate  Incentives  0.000000e+00   
2545  Mixed Scenario 2045_4_modest learning rate  Incentives  0.000000e+00   
2546  Mixed Scenario 2045_4_modest learning rate  Incentives  0.000000e+00   
2547  Mixed Scenario 2045_4_modest learning rate  Incentives  0.000000e+00   

      Year  line_id                               long_sce_name  \
0     2018        0                                    Baseline   
1     2019        0                                    Baseline   
2     2020        0                                    Baseline   
3     2021        0                                    Baseline   
4     2022        0                                    Baseline   
...    ...      ...                                         ...   
2543  2041        4  Mixed Scenario 2045 (modest learning rate)   
2544  2042        4  Mixed Scenario 2045 (modest learning rate)   
2545  2043        4  Mixed Scenario 2045 (modest learning rate)   
2546  2044        4  Mixed Scenario 2045 (modest learning rate)   
2547  2045        4  Mixed Scenario 2045 (modest learning rate)   

           short_sce_name  
0                Baseline  
1                Baseline  
2                Baseline  
3                Baseline  
4                Baseline  
...                   ...  
2543  Mixed Scenario 2045  
2544  Mixed Scenario 2045  
2545  Mixed Scenario 2045  
2546  Mixed Scenario 2045  
2547  Mixed Scenario 2045  

[2548 rows x 7 columns]

In [433]:
for sce_comp in sce_comps_short + sce_comps_long:
    plot_subgroup_result_single_yr_compare_scenarios(df_emissions_sector, sce_comp, "Sectoral Emissions", "Tonnes CO2e", 2045, sector_color_map)

In [434]:
plot_subgroup_result_over_time(df_emissions_sector, "Emissions by Sector", "Tonnes CO2e", sector_color_map, "bar")

In [435]:
df_costs_sector = form_df_result_by_subgroup(df, sector_map, 'Social Costs')
df_costs_sector

Scenario    Subgroup         Value  \
0                                 Baseline_0_nan    Industry  3.734845e+10   
1                                 Baseline_0_nan    Industry  3.678330e+10   
2                                 Baseline_0_nan    Industry  3.626703e+10   
3                                 Baseline_0_nan    Industry  3.579643e+10   
4                                 Baseline_0_nan    Industry  3.536706e+10   
...                                          ...         ...           ...   
2543  Mixed Scenario 2045_4_modest learning rate  Incentives -1.062587e+10   
2544  Mixed Scenario 2045_4_modest learning rate  Incentives -1.077761e+10   
2545  Mixed Scenario 2045_4_modest learning rate  Incentives -1.094160e+10   
2546  Mixed Scenario 2045_4_modest learning rate  Incentives -1.079721e+10   
2547  Mixed Scenario 2045_4_modest learning rate  Incentives -1.070832e+10   

      Year  line_id                               long_sce_name  \
0     2018        0                                    Baseline   
1     2019        0                                    Baseline   
2     2020        0                                    Baseline   
3     2021        0                                    Baseline   
4     2022        0                                    Baseline   
...    ...      ...                                         ...   
2543  2041        4  Mixed Scenario 2045 (modest learning rate)   
2544  2042        4  Mixed Scenario 2045 (modest learning rate)   
2545  2043        4  Mixed Scenario 2045 (modest learning rate)   
2546  2044        4  Mixed Scenario 2045 (modest learning rate)   
2547  2045        4  Mixed Scenario 2045 (modest learning rate)   

           short_sce_name  
0                Baseline  
1                Baseline  
2                Baseline  
3                Baseline  
4                Baseline  
...                   ...  
2543  Mixed Scenario 2045  
2544  Mixed Scenario 2045  
2545  Mixed Scenario 2045  
2546  Mixed Scenario 2045  
2547  Mixed Scenario 2045  

[2548 rows x 7 columns]

In [436]:
def npv_it (df_in, disc_rate=0.05):
    
    yrs = np.sort(df_in['Year'].unique())
    base_yr = yrs[0]
    
    # discount all costs
    for key, dfg in df_in.groupby(by=['Scenario', 'Subgroup', 'Year']):
        sce, subg, yr = key
        mask = np.array(
            (df_in['Scenario'] == sce) & 
            (df_in['Subgroup'] == subg) &
            (df_in['Year'] == yr)
        )
        ids = list(np.where(mask)[0])
        df_in.iloc[ids, df_in.columns.get_loc('Value')] = dfg['Value'] / (1 + disc_rate)**(yr - base_yr)
    
    return df_in
    
def cumsum_it (df_in):
    # sum all discounted costs
    for key, dfg in df_in.groupby(by=['Scenario', 'Subgroup']):
        sce, subg = key
        mask = np.array(
            (df_in['Scenario'] == sce) & 
            (df_in['Subgroup'] == subg)
        )
        ids = list(np.where(mask)[0])
        df_in.iloc[ids, df_in.columns.get_loc('Value')] = df_in.iloc[ids, df_in.columns.get_loc('Value')].cumsum(axis=0)
    
    return df_in
    

def marginalize_it (df_in, relative_to="LEAP Version CARB Reference_0_nan"):
    for subg, yr in itertools.product(df_in['Subgroup'].unique(), df_in['Year'].unique()):
        
        # create mask for relevant values in the relative_to scenario
        relative_to_mask = np.array(
            (df_in['Scenario'] == relative_to) &
            (df_in['Subgroup'] == subg) &
            (df_in['Year'] == yr)
        )
        relative_to_ids = list(np.where(relative_to_mask)[0])
        
        # create mask for the values that are being marginalized
        marginalize_mask = np.array(
            (df_in['Subgroup'] == subg) &
            (df_in['Year'] == yr)
        )
        marginalize_ids = list(np.where(marginalize_mask)[0])
        
        df_in.iloc[marginalize_ids, df_in.columns.get_loc('Value')] -= float(df_in.iloc[relative_to_ids, df_in.columns.get_loc('Value')])

    return df_in

In [437]:
df_costs_sector_marginal = marginalize_it(df_costs_sector)
df_costs_sector_marginal

Scenario    Subgroup         Value  \
0                                 Baseline_0_nan    Industry  0.000000e+00   
1                                 Baseline_0_nan    Industry  2.219345e+08   
2                                 Baseline_0_nan    Industry  1.319659e+09   
3                                 Baseline_0_nan    Industry  1.836122e+09   
4                                 Baseline_0_nan    Industry  2.389605e+09   
...                                          ...         ...           ...   
2543  Mixed Scenario 2045_4_modest learning rate  Incentives  2.971902e+09   
2544  Mixed Scenario 2045_4_modest learning rate  Incentives  3.453569e+09   
2545  Mixed Scenario 2045_4_modest learning rate  Incentives  3.934059e+09   
2546  Mixed Scenario 2045_4_modest learning rate  Incentives  4.715730e+09   
2547  Mixed Scenario 2045_4_modest learning rate  Incentives  5.463770e+09   

      Year  line_id                               long_sce_name  \
0     2018        0                                    Baseline   
1     2019        0                                    Baseline   
2     2020        0                                    Baseline   
3     2021        0                                    Baseline   
4     2022        0                                    Baseline   
...    ...      ...                                         ...   
2543  2041        4  Mixed Scenario 2045 (modest learning rate)   
2544  2042        4  Mixed Scenario 2045 (modest learning rate)   
2545  2043        4  Mixed Scenario 2045 (modest learning rate)   
2546  2044        4  Mixed Scenario 2045 (modest learning rate)   
2547  2045        4  Mixed Scenario 2045 (modest learning rate)   

           short_sce_name  
0                Baseline  
1                Baseline  
2                Baseline  
3                Baseline  
4                Baseline  
...                   ...  
2543  Mixed Scenario 2045  
2544  Mixed Scenario 2045  
2545  Mixed Scenario 2045  
2546  Mixed Scenario 2045  
2547  Mixed Scenario 2045  

[2548 rows x 7 columns]

In [438]:
plot_subgroup_result_over_time(df_costs_sector_marginal, "Marginal Costs by Sector", "USD", sector_color_map, "bar")

In [439]:
df_costs_sector_marginal_discounted = npv_it(df_costs_sector_marginal)
df_costs_sector_marginal_discounted


Scenario    Subgroup         Value  \
0                                 Baseline_0_nan    Industry  0.000000e+00   
1                                 Baseline_0_nan    Industry  2.113662e+08   
2                                 Baseline_0_nan    Industry  1.196970e+09   
3                                 Baseline_0_nan    Industry  1.586111e+09   
4                                 Baseline_0_nan    Industry  1.965934e+09   
...                                          ...         ...           ...   
2543  Mixed Scenario 2045_4_modest learning rate  Incentives  9.675660e+08   
2544  Mixed Scenario 2045_4_modest learning rate  Incentives  1.070841e+09   
2545  Mixed Scenario 2045_4_modest learning rate  Incentives  1.161739e+09   
2546  Mixed Scenario 2045_4_modest learning rate  Incentives  1.326255e+09   
2547  Mixed Scenario 2045_4_modest learning rate  Incentives  1.463462e+09   

      Year  line_id                               long_sce_name  \
0     2018        0                                    Baseline   
1     2019        0                                    Baseline   
2     2020        0                                    Baseline   
3     2021        0                                    Baseline   
4     2022        0                                    Baseline   
...    ...      ...                                         ...   
2543  2041        4  Mixed Scenario 2045 (modest learning rate)   
2544  2042        4  Mixed Scenario 2045 (modest learning rate)   
2545  2043        4  Mixed Scenario 2045 (modest learning rate)   
2546  2044        4  Mixed Scenario 2045 (modest learning rate)   
2547  2045        4  Mixed Scenario 2045 (modest learning rate)   

           short_sce_name  
0                Baseline  
1                Baseline  
2                Baseline  
3                Baseline  
4                Baseline  
...                   ...  
2543  Mixed Scenario 2045  
2544  Mixed Scenario 2045  
2545  Mixed Scenario 2045  
2546  Mixed Scenario 2045  
2547  Mixed Scenario 2045  

[2548 rows x 7 columns]

In [440]:
plot_subgroup_result_over_time(df_costs_sector_marginal_discounted, "Marginal Costs by Sector (discounted)", "USD", sector_color_map, "bar")

In [441]:
df_costs_sector_marginal_discounted_cumsum = cumsum_it(df_costs_sector_marginal_discounted)
df_costs_sector_marginal_discounted_cumsum

Scenario    Subgroup         Value  \
0                                 Baseline_0_nan    Industry  0.000000e+00   
1                                 Baseline_0_nan    Industry  2.113662e+08   
2                                 Baseline_0_nan    Industry  1.408336e+09   
3                                 Baseline_0_nan    Industry  2.994447e+09   
4                                 Baseline_0_nan    Industry  4.960381e+09   
...                                          ...         ...           ...   
2543  Mixed Scenario 2045_4_modest learning rate  Incentives  1.008576e+10   
2544  Mixed Scenario 2045_4_modest learning rate  Incentives  1.115661e+10   
2545  Mixed Scenario 2045_4_modest learning rate  Incentives  1.231834e+10   
2546  Mixed Scenario 2045_4_modest learning rate  Incentives  1.364460e+10   
2547  Mixed Scenario 2045_4_modest learning rate  Incentives  1.510806e+10   

      Year  line_id                               long_sce_name  \
0     2018        0                                    Baseline   
1     2019        0                                    Baseline   
2     2020        0                                    Baseline   
3     2021        0                                    Baseline   
4     2022        0                                    Baseline   
...    ...      ...                                         ...   
2543  2041        4  Mixed Scenario 2045 (modest learning rate)   
2544  2042        4  Mixed Scenario 2045 (modest learning rate)   
2545  2043        4  Mixed Scenario 2045 (modest learning rate)   
2546  2044        4  Mixed Scenario 2045 (modest learning rate)   
2547  2045        4  Mixed Scenario 2045 (modest learning rate)   

           short_sce_name  
0                Baseline  
1                Baseline  
2                Baseline  
3                Baseline  
4                Baseline  
...                   ...  
2543  Mixed Scenario 2045  
2544  Mixed Scenario 2045  
2545  Mixed Scenario 2045  
2546  Mixed Scenario 2045  
2547  Mixed Scenario 2045  

[2548 rows x 7 columns]

In [442]:
for sce_comp in sce_comps_short + sce_comps_long:
    plot_subgroup_result_single_yr_compare_scenarios(
        df_costs_sector_marginal_discounted_cumsum, 
        sce_comp, "Sectoral Cumulative Costs", "USD", 2045, sector_color_map)

## Load shapes

In [443]:
df_shapes_raw = pd.read_excel(input_path / "results.xlsx", sheet_name="Shapes")
id_cols = ['Index', 'Year', 'Scenario', 'Result Variable', 'Branch']
hour_cols = list(set(df_shapes_raw.columns) - set(id_cols))

df_shapes = pd.DataFrame(columns=['Year', 'Hour', 'Scenario', 'Branch', 'Result Variable', 'Result'])


for row in df_shapes_raw.index:
    df_to_add = pd.DataFrame(columns=['Year', 'Hour', 'Scenario', 'Branch', 'Result Variable', 'Result'])
    df_to_add['Hour'] = pd.Series(hour_cols)
    df_to_add['Result'] = pd.Series(df_shapes_raw.loc[row, hour_cols]).reset_index(drop=True)
    df_to_add[['Year', 'Scenario', 'Branch', 'Result Variable']] = df_shapes_raw.loc[row, ['Year', 'Scenario', 'Branch', 'Result Variable']]
    df_shapes = pd.concat([df_shapes, df_to_add], ignore_index=True)
    
df_shapes = cleanup_scenario_names(df_shapes)

Year Hour                                    Scenario  \
0      2018    1                          Today Actual_0_nan   
1      2018    2                          Today Actual_0_nan   
2      2018    3                          Today Actual_0_nan   
3      2018    4                          Today Actual_0_nan   
4      2018    5                          Today Actual_0_nan   
...     ...  ...                                         ...   
61051  2045  284  Med Elec RPS 100 NoNGCCSHydroNuclear_0_nan   
61052  2045  285  Med Elec RPS 100 NoNGCCSHydroNuclear_0_nan   
61053  2045  286  Med Elec RPS 100 NoNGCCSHydroNuclear_0_nan   
61054  2045  287  Med Elec RPS 100 NoNGCCSHydroNuclear_0_nan   
61055  2045  288  Med Elec RPS 100 NoNGCCSHydroNuclear_0_nan   

                               Branch   Result Variable       Result  \
0                                 NaN        Load Shape  21064.62975   
1                                 NaN        Load Shape     20341.39   
2                                 NaN        Load Shape     19934.47   
3                                 NaN        Load Shape     19841.62   
4                                 NaN        Load Shape     20279.83   
...                               ...               ...          ...   
61051  Electricity Production Optimal  Generation Shape     45002.31   
61052  Electricity Production Optimal  Generation Shape     43024.49   
61053  Electricity Production Optimal  Generation Shape     40066.25   
61054  Electricity Production Optimal  Generation Shape     33759.54   
61055  Electricity Production Optimal  Generation Shape     32919.69   

                             short_sce_name  line_id long_sce_name  
0                              Today Actual        0           nan  
1                              Today Actual        0           nan  
2                              Today Actual        0           nan  
3                              Today Actual        0           nan  
4                              Today Actual        0           nan  
...                                     ...      ...           ...  
61051  Med Elec RPS 100 NoNGCCSHydroNuclear        0           nan  
61052  Med Elec RPS 100 NoNGCCSHydroNuclear        0           nan  
61053  Med Elec RPS 100 NoNGCCSHydroNuclear        0           nan  
61054  Med Elec RPS 100 NoNGCCSHydroNuclear        0           nan  
61055  Med Elec RPS 100 NoNGCCSHydroNuclear        0           nan  

[61056 rows x 9 columns]

In [444]:
# note: only doing this because the results file currently has different scenarios in the load shapes vs. other results
sce_loads = [
    ["High Elec RPS 80_0_nan", "Med Elec RPS 80_0_nan", "Low Elec RPS 80_0_nan"],
    ["Med Elec Low Shift RPS 100_0_nan", "Med Elec High Shift RPS 100_0_nan", "Med Elec Medium Shift RPS 100_0_nan"]
]

months = ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']


for sce_comp in sce_loads:
    fig = px.line(
        df_shapes[(df_shapes['Scenario'].isin(sce_comp)) &
                  (df_shapes['Year'] == 2045) &
                  (df_shapes['Result Variable'] == 'Load Shape')],
        x='Hour',
        y='Result',
        color='long_sce_name',
        #todo: pass in color_dict so colors are consistent
    )
    fig.update_layout(
        title='Load Shape',
        xaxis_title='Representative Day of Month',
        yaxis_title='MW',
        legend_title='Scenario',
        xaxis=dict(
            tickmode='array',
            tickvals=np.arange(12,289,24),
            ticktext=months,
            showgrid=False,
            minor=dict(
                tickvals=np.arange(0,289,24),
                showgrid=True,
                gridcolor='#FFFFFF'
            )
        )
    )
    
    month_ends = np.arange(0, 289, 24)
    for i, (x0, x1) in enumerate(zip(month_ends, month_ends[1:])):
        if i % 2 == 0:
            continue
        else:
            fig.add_vrect(x0=x0, x1=x1, line_width=0, fillcolor='grey', opacity=0.1)
    
    global IMAGE_PATH
    global IMAGE_COUNT
    fig.write_image(IMAGE_PATH / f"fig_{IMAGE_COUNT}.pdf")
    IMAGE_COUNT += 1
    
    fig.show()

## TODO: RNG / Renewable diesel consumption vs potential

In [10]:
from PyPDF2 import PdfMerger

merger = PdfMerger()
for f in [f for f in os.listdir(IMAGE_PATH) if f.endswith(".pdf")]:
    absfile = os.path.join(IMAGE_PATH, f)
    merger.append(open(absfile, 'rb'))
    
with open(IMAGE_PATH / "merged.pdf", "wb") as fout:
    merger.write(fout)
    